## Import Packages

In [112]:
from __future__ import (absolute_import, division, print_function,
                        unicode_literals)

import argparse
import datetime
import math

import pandas as pd
import numpy as np

from matplotlib import pyplot as plt

# The above could be sent to an independent module
import backtrader as bt
import backtrader.feeds as btfeeds
import backtrader.indicators as btind

import statsmodels.tsa.stattools as smts
import statsmodels.api as sm

import datetime as dt

** TODO **

- ur first step is to read all data from NYSE as dataframes(narrow down to NYSE for now)
- look at the starting date of all dataframes, pick the max, and then segment all dataframe to make sure they start on the same day (u can refer to notebook 4c "generate_pairs_df" to see how this can be done)
- iterate through all NC2 pair, and calculate their sum of squared difference for each pair, then pick K smallest pairs, save them somewhere (YOU DONT HAVE TO WRITE THE CODE FOR THIS, ITS ALRDY WRITTEN BY GORDON IN **pair_selectory.py**, just figure out how to pass the price data of all N stocks in as the right format, if i rmb correctly the format is, each column is the price of 1 stock, column name is the stock name, so u need to aggregate close price of all N stocks into 1 dataframe)
- for each pair, backtest and save result metrics (initial portfolio val, final porfolio val, number of timeouts) to a pandas (dont just print lol)
- make sure to save the name of the pair also lol (like 'GOOG-GOOGL')
- write the pandas to a csv 
- to read all csv files from a directory, u need to import glob and os (check sample code in notebook 4a to see how i read all csv files from one directory as a list)


## Read data

In [120]:
import glob
import os

# get file names of all csv files with nyse stock prices 
nyse_csv_paths = sorted(glob.glob("../ib-data/nyse/*.csv"))
N_STOCKS = len(nyse_csv_paths)

In [121]:
data = {}
MIN_SIZE = 84*252*2
N_STOCKS_TAKEN = 0

for path in nyse_csv_paths:
    # get the file names
    filename = os.path.basename(path)
    filename_without_ext = os.path.splitext(filename)[0]
    
    # read the csv file as dataframe
    df = pd.read_csv(path)
    df['date'] = pd.to_datetime(df['date'], format='%Y-%m-%d %H:%M:%S')
    
    # if price history is long enough, we take it
    if len(df) >= MIN_SIZE:
        data[filename_without_ext] = df 
        N_STOCKS_TAKEN += 1

In [122]:
print("N_STOCKS = " + str(N_STOCKS))
print("N_STOCKS_TAKEN = " + str(N_STOCKS_TAKEN))

N_STOCKS = 170
N_STOCKS_TAKEN = 131


## Ensure all prices have same start date

In [134]:
# get max starting date
MAX_DATE = pd.Timestamp.min

for key in data.keys():
    # reset index 
    data[key] = data[key].reset_index(drop=True)
    
    # max
    MAX_DATE = max(MAX_DATE, data[key]['date'][0])
    
# take subset of all dataframes
for key in data.keys():
    data[key] = data[key][data[key]['date'] >= MAX_DATE]
    
    # reset index 
    data[key] = data[key].reset_index(drop=True)

## Aggregate prices

In [135]:
from pair_selector import *

In [136]:
# aggregate all close prices
close_price_df = pd.DataFrame()

for key in data.keys():
    close_price_df[key] = data[key]['close']

### Verify

In [137]:
# check if there are null values
close_price_df.isnull().values.any()

True

## Get K best pairs

Assuming we take the top 5% pairs ... 

In [147]:
N = len(data.keys())
print(int(N*(N-1)/2), 'pairs')

K = int(0.05 * N * (N-1) / 2)
print(K)

8515 pairs
425


In [151]:
TRAIN_PERIOD = 84*50

good_pairs = intersection(close_price_df[0:TRAIN_PERIOD], test_df=None, n = K, plot=False)
good_pairs

[('JBT', 'MAN'),
 ('NEWR', 'QTM'),
 ('GHM', 'MAN'),
 ('BHE', 'INST'),
 ('FDS', 'VMW'),
 ('CW', 'MCRN'),
 ('FIT', 'SSTK'),
 ('CW', 'TDC'),
 ('AAN', 'INST'),
 ('AAN', 'MSI'),
 ('LEAF', 'TBI'),
 ('MAN', 'ZEN'),
 ('SQ', 'TNC'),
 ('ELLI', 'PKE'),
 ('LLL', 'WIT'),
 ('ASGN', 'CLGX'),
 ('CLGX', 'GHM'),
 ('AAN', 'SHOP'),
 ('ANET', 'NEWR'),
 ('GLOB', 'WUBA'),
 ('IPHI', 'PAYC'),
 ('CW', 'PAYC'),
 ('GDDY', 'INST'),
 ('HPE', 'INST'),
 ('AL', 'KAI'),
 ('AUO', 'KAI'),
 ('HPE', 'SSTK'),
 ('NEWR', 'PANW'),
 ('GWRE', 'URI'),
 ('INXN', 'MXL'),
 ('BHE', 'DDD'),
 ('CLS', 'LEAF'),
 ('AYR', 'LEAF'),
 ('INXN', 'LLL'),
 ('JNPR', 'NEWR'),
 ('CTS', 'KAI'),
 ('JNPR', 'RENN'),
 ('AAN', 'SPXC'),
 ('HPE', 'LEAF'),
 ('BHE', 'STM'),
 ('HPQ', 'HUBS'),
 ('HUBS', 'TDC'),
 ('BHE', 'NEWR'),
 ('EVTC', 'LEAF'),
 ('KAI', 'MCRN'),
 ('NOK', 'TBI'),
 ('ANET', 'TWLO'),
 ('DDD', 'RENN'),
 ('EXTN', 'RST'),
 ('FDS', 'MAN'),
 ('LLL', 'SXI'),
 ('PANW', 'VEEV'),
 ('BOX', 'NEWR'),
 ('DOV', 'INXN'),
 ('ETN', 'INXN'),
 ('HHS', 'TGH'),
 ('

## Strategy

In [184]:
class SinglePair(bt.Strategy):
    params = dict (
        period=84,
    )

    def log(self, txt, dt=None):        
        dt = dt or self.data.datetime[0]
        dt = bt.num2date(dt)
        print('%s, %s' % (dt.isoformat(), txt))

    def notify_order(self, order):
        if order.status in [bt.Order.Submitted, bt.Order.Accepted]:
            return  # Await further notifications

        if order.status == order.Completed:
            if order.isbuy():
                buytxt = 'BUY COMPLETE, %.2f' % order.executed.price
                self.log(buytxt, order.executed.dt)
                self.incur_commission(order.executed.price, order.executed.size)
            else:
                selltxt = 'SELL COMPLETE, %.2f' % order.executed.price
                self.log(selltxt, order.executed.dt)
                self.incur_commission(order.executed.price, order.executed.size)

        elif order.status in [order.Expired, order.Canceled, order.Margin]:
            self.log('%s ,' % order.Status[order.status])
            pass  # Simply log

        # Allow new orders
        self.orderid = None

    def __init__(self):
        # To control operation entries
        self.orderid = None
        self.qty1 = 0
        self.qty2 = 0
        self.period = self.p.period
        self.upper_limit = 2.0
        self.lower_limit = -2.0
        self.up_medium = 0.5
        self.low_medium = -0.5
        self.status = 0
        self.exposure = 200000
    
        self.zscore = None
        self.adf_pvalue = None
        self.intercept = None
        self.slope = None
        self.resid_mean = None
        self.resid_std = None
        self.spread = None
        self.zscore = None
        
        self.open_pos_duration = 0
        self.n_timeouts = 0

    def next(self):
        print("--------------------------------------------------------------------")
        print("Current cash: %.2f" % self.broker.get_cash())
        print("Portfolio value: %.2f" % self.broker.getvalue())
        
        if min(len(self.data0), len(self.data1)) < self.period:
            return
        
        if self.orderid:
            return  # if an order is active, no new orders are allowed
        
        ##################################################################################################
        # COMPUTE UPPER AND LOWER LIMITS                                                                 #
        ##################################################################################################
        Y = pd.Series(self.data0.get(size=self.period)[0:-1])
        X = pd.Series(self.data1.get(size=self.period)[0:-1])
        
        self.spread = (self.data0[0] - self.data1[0])
        
        if self.status == 0:
            self.spread_mean = (Y - X).mean()
            self.spread_std = (Y - X).std()

            self.upper_limit = self.spread_mean + 2 * self.spread_std
            self.lower_limit = self.spread_mean - 2 * self.spread_std
            self.up_medium = self.spread_mean + 0.5 * self.spread_std
            self.low_medium = self.spread_mean - 0.5 * self.spread_std
        
        ##################################################################################################
        # LOGGING                                                                                        #
        ##################################################################################################
        print("--------------------------------------------------------------------")
        
        print('Strategy  len:', len(self))
        print('Data0 len:', len(self.data0))
        print('Data1 len:', len(self.data1))
        
        print('Data0 dt:', dt.datetime.strftime(data0.datetime.datetime(),'%Y-%m-%d %H:%M:%S'))
        print('Data1 dt:', dt.datetime.strftime(data1.datetime.datetime(),'%Y-%m-%d %H:%M:%S'))

        print('Data0 dt:', dt.datetime.strftime(data0.datetime.datetime(),'%Y-%m-%d %H:%M:%S'))
        print('Data1 dt:', dt.datetime.strftime(data1.datetime.datetime(),'%Y-%m-%d %H:%M:%S'))
        
        print('status is', self.status)
    
        ##################################################################################################
        # STRATEGY LOGIC                                                                                 #
        ##################################################################################################
        if self.status == 0:
            # "NO position" status
            self.open_pos_duration = 0
            
            if self.spread > self.upper_limit:
                self.short_spread()
            elif self.spread < self.lower_limit:
                self.long_spread()
     
        elif self.status == 1:
            # "SHORT the spread" status
            self.open_pos_duration += 1
            
            if self.spread < self.lower_limit:
                self.long_spread()
            elif self.spread < self.up_medium:
                self.exit_spread()
                self.status = 0
        
        elif self.status == 2:
            # "LONG the spread" status
            self.open_pos_duration += 1
            
            if self.spread > self.upper_limit:
                self.short_spread()
            elif self.spread > self.low_medium:
                self.exit_spread()
                self.status = 0
                
        # TIMEOUT condition
        if self.open_pos_duration > 84:
            self.exit_spread()
            self.n_timeouts += 1
            self.status = 0
    
    def short_spread(self):
        value = 0.5 * self.exposure  
        x = int(value / (self.data0.close))  
        y = int(value / (self.data1.close))  
        
        print('x + self.qty1 is', x + self.qty1)
        print('y + self.qty2 is', y + self.qty2)

        # Placing the order
        self.log('SELL CREATE %s, price = %.2f, qty = %d' % ("STOCK 1", self.data0.close[0], x + self.qty1))
        self.sell(data=self.data0, size=(x + self.qty1))  # Place an order for buying y + qty2 shares
        self.log('BUY CREATE %s, price = %.2f, qty = %d' % ("STOCK 2", self.data1.close[0], y + self.qty2))
        self.buy(data=self.data1, size=(y + self.qty2))  # Place an order for selling x + qty1 shares

        # Updating the counters with new value
        self.qty1 = x  
        self.qty2 = y  
        
        # update flags
        self.status = 1
        self.open_pos_duration = 0
    
    def long_spread(self):
        # Calculating the number of shares for each stock
        value = 0.5 * self.exposure 
        x = int(value / (self.data0.close)) 
        y = int(value / (self.data1.close)) 
        
        print('x + self.qty1 is', x + self.qty1)
        print('y + self.qty2 is', y + self.qty2)

        # Place the order
        self.log('BUY CREATE %s, price = %.2f, qty = %d' % ("STOCK 1", self.data0.close[0], x + self.qty1))
        self.buy(data=self.data0, size=(x + self.qty1))  # Place an order for buying x + qty1 shares
        self.log('SELL CREATE %s, price = %.2f, qty = %d' % ("STOCK 2", self.data1.close[0], y + self.qty2))
        self.sell(data=self.data1, size=(y + self.qty2))  # Place an order for selling y + qty2 shares

        # Updating the counters with new value
        self.qty1 = x 
        self.qty2 = y 
        
        # update flags
        self.status = 2  
        self.open_pos_duration = 0
    
    def exit_spread(self):
        # Exit position
        self.log('CLOSE position %s, price = %.2f' % ("STOCK 1", self.data0.close[0]))
        self.close(self.data0)
        self.log('CLOSE position %s, price = %.2f' % ("STOCK 2", self.data1.close[0]))
        self.close(self.data1)
        
        # update counters
        self.qty1 = 0
        self.qty2 = 0
        
        # update flags
        self.status = 0
        self.open_pos_duration = 0
        
    def incur_commission(self, price, qty):
        qty = abs(qty)
        commission = min(max(1, 0.005*qty), 0.01*price*qty)
        print('Commission of ' + str(commission) + 'USD incurred.')
        self.broker.add_cash(-1*commission)
    
    def stop(self):
        print('==================================================')
        print('Starting Value: %.2f' % self.broker.startingcash)
        print('Ending   Value: %.2f' % self.broker.getvalue())
        print('Number of timeouts: %.2f' % self.n_timeouts)
        print('==================================================')

- This is a class for backtesting (dist method) on a single pair
- look at notebook 4b to see how to initialize a cerebro object, pass 2 data feeds in and run backtest

## Backtest on all pairs

In [179]:
class PandasData(bt.feed.DataBase):
    '''
    The ``dataname`` parameter inherited from ``feed.DataBase`` is the pandas
    DataFrame
    '''

    params = (
        ('datetime', 0),
        ('open', -1),
        ('high', -1),
        ('low', -1),
        ('close', -1),
        ('volume', -1),
        ('openinterest', -1),
    )

In [ ]:
TEST_PERIOD = 84*252
results = []

for pair in good_pairs:
    # get names of both stock
    stk0, stk1 = pair
    
    # get data of both stock
    stk0_df, stk1_df = data[stk0], data[stk1]
    stk0_df_test, stk1_df_test = stk0_df[TRAIN_PERIOD:TRAIN_PERIOD + TEST_PERIOD], stk1_df[TRAIN_PERIOD:TRAIN_PERIOD + TEST_PERIOD]
    
    # Create a cerebro
    cerebro = bt.Cerebro()
    
    # Create data feeds
    data0 = bt.feeds.PandasData(dataname=stk0_df_test, timeframe=(bt.TimeFrame.Minutes), datetime=0)
    data1 = bt.feeds.PandasData(dataname=stk1_df_test, timeframe=(bt.TimeFrame.Minutes), datetime=0)
    
    # add data feeds to cerebro
    cerebro.adddata(data0)
    cerebro.adddata(data1)

    # Add the strategy
    cerebro.addstrategy(SinglePair)

    # Add Sharpe Ratio
    cerebro.addanalyzer(bt.analyzers.SharpeRatio, _name='mysharpe')

    # Add the commission - only stocks like a for each operation
    cerebro.broker.setcash(1000000)

    # And run it
    strat = cerebro.run()
    
    # get metrics
    sharperatio = strat[0].analyzers.mysharpe.get_analysis()['sharperatio']
    startcash = cerebro.getbroker().startingcash
    endcash = cerebro.getbroker().getvalue()
    
    results.append((stk0 + "-" + stk1, sharperatio, startcash, endcash))

--------------------------------------------------------------------
Current cash: 1000000.00
Portfolio value: 1000000.00
--------------------------------------------------------------------
Current cash: 1000000.00
Portfolio value: 1000000.00
--------------------------------------------------------------------
Current cash: 1000000.00
Portfolio value: 1000000.00
--------------------------------------------------------------------
Current cash: 1000000.00
Portfolio value: 1000000.00
--------------------------------------------------------------------
Current cash: 1000000.00
Portfolio value: 1000000.00
--------------------------------------------------------------------
Current cash: 1000000.00
Portfolio value: 1000000.00
--------------------------------------------------------------------
Current cash: 1000000.00
Portfolio value: 1000000.00
--------------------------------------------------------------------
Current cash: 1000000.00
Portfolio value: 1000000.00
------------------------

Data0 dt: 2016-10-01 01:30:00
Data1 dt: 2016-10-01 01:30:00
Data0 dt: 2016-10-01 01:30:00
Data1 dt: 2016-10-01 01:30:00
status is 2
--------------------------------------------------------------------
Current cash: 999933.81
Portfolio value: 999673.63
--------------------------------------------------------------------
Strategy  len: 133
Data0 len: 133
Data1 len: 133
Data0 dt: 2016-10-01 01:35:00
Data1 dt: 2016-10-01 01:35:00
Data0 dt: 2016-10-01 01:35:00
Data1 dt: 2016-10-01 01:35:00
status is 2
--------------------------------------------------------------------
Current cash: 999933.81
Portfolio value: 999565.05
--------------------------------------------------------------------
Strategy  len: 134
Data0 len: 134
Data1 len: 134
Data0 dt: 2016-10-01 01:40:00
Data1 dt: 2016-10-01 01:40:00
Data0 dt: 2016-10-01 01:40:00
Data1 dt: 2016-10-01 01:40:00
status is 2
--------------------------------------------------------------------
Current cash: 999933.81
Portfolio value: 999607.09
--------

Data1 dt: 2016-10-04 22:45:00
Data0 dt: 2016-10-04 22:45:00
Data1 dt: 2016-10-04 22:45:00
status is 2
--------------------------------------------------------------------
Current cash: 1000227.54
Portfolio value: 999303.74
--------------------------------------------------------------------
Strategy  len: 256
Data0 len: 256
Data1 len: 256
Data0 dt: 2016-10-04 22:50:00
Data1 dt: 2016-10-04 22:50:00
Data0 dt: 2016-10-04 22:50:00
Data1 dt: 2016-10-04 22:50:00
status is 2
--------------------------------------------------------------------
Current cash: 1000227.54
Portfolio value: 998980.74
--------------------------------------------------------------------
Strategy  len: 257
Data0 len: 257
Data1 len: 257
Data0 dt: 2016-10-04 22:55:00
Data1 dt: 2016-10-04 22:55:00
Data0 dt: 2016-10-04 22:55:00
Data1 dt: 2016-10-04 22:55:00
status is 2
--------------------------------------------------------------------
Current cash: 1000227.54
Portfolio value: 999100.04
-----------------------------------

--------------------------------------------------------------------
Strategy  len: 368
Data0 len: 368
Data1 len: 368
Data0 dt: 2016-10-06 01:40:00
Data1 dt: 2016-10-06 01:40:00
Data0 dt: 2016-10-06 01:40:00
Data1 dt: 2016-10-06 01:40:00
status is 1
--------------------------------------------------------------------
Current cash: 1000119.83
Portfolio value: 999892.20
--------------------------------------------------------------------
Strategy  len: 369
Data0 len: 369
Data1 len: 369
Data0 dt: 2016-10-06 01:45:00
Data1 dt: 2016-10-06 01:45:00
Data0 dt: 2016-10-06 01:45:00
Data1 dt: 2016-10-06 01:45:00
status is 1
--------------------------------------------------------------------
Current cash: 1000119.83
Portfolio value: 999748.71
--------------------------------------------------------------------
Strategy  len: 370
Data0 len: 370
Data1 len: 370
Data0 dt: 2016-10-06 01:50:00
Data1 dt: 2016-10-06 01:50:00
Data0 dt: 2016-10-06 01:50:00
Data1 dt: 2016-10-06 01:50:00
status is 1
--------

Data1 dt: 2016-10-07 21:45:00
Data0 dt: 2016-10-07 21:45:00
Data1 dt: 2016-10-07 21:45:00
status is 1
--------------------------------------------------------------------
Current cash: 1001645.05
Portfolio value: 1001999.71
--------------------------------------------------------------------
Strategy  len: 478
Data0 len: 478
Data1 len: 478
Data0 dt: 2016-10-07 21:50:00
Data1 dt: 2016-10-07 21:50:00
Data0 dt: 2016-10-07 21:50:00
Data1 dt: 2016-10-07 21:50:00
status is 1
--------------------------------------------------------------------
Current cash: 1001645.05
Portfolio value: 1001932.26
--------------------------------------------------------------------
Strategy  len: 479
Data0 len: 479
Data1 len: 479
Data0 dt: 2016-10-07 21:55:00
Data1 dt: 2016-10-07 21:55:00
Data0 dt: 2016-10-07 21:55:00
Data1 dt: 2016-10-07 21:55:00
status is 1
--------------------------------------------------------------------
Current cash: 1001645.05
Portfolio value: 1002026.90
--------------------------------

...

Data1 dt: 2017-07-22 02:00:00
Data0 dt: 2017-07-22 02:00:00
Data1 dt: 2017-07-22 02:00:00
status is 0
--------------------------------------------------------------------
Current cash: 1033148.92
Portfolio value: 1033148.92
--------------------------------------------------------------------
Strategy  len: 15823
Data0 len: 15823
Data1 len: 15823
Data0 dt: 2017-07-22 02:05:00
Data1 dt: 2017-07-22 02:05:00
Data0 dt: 2017-07-22 02:05:00
Data1 dt: 2017-07-22 02:05:00
status is 0
--------------------------------------------------------------------
Current cash: 1033148.92
Portfolio value: 1033148.92
--------------------------------------------------------------------
Strategy  len: 15824
Data0 len: 15824
Data1 len: 15824
Data0 dt: 2017-07-22 02:10:00
Data1 dt: 2017-07-22 02:10:00
Data0 dt: 2017-07-22 02:10:00
Data1 dt: 2017-07-22 02:10:00
status is 0
--------------------------------------------------------------------
Current cash: 1033148.92
Portfolio value: 1033148.92
--------------------

Portfolio value: 1026989.12
--------------------------------------------------------------------
Strategy  len: 15944
Data0 len: 15944
Data1 len: 15944
Data0 dt: 2017-07-25 23:10:00
Data1 dt: 2017-07-25 23:10:00
Data0 dt: 2017-07-25 23:10:00
Data1 dt: 2017-07-25 23:10:00
status is 1
--------------------------------------------------------------------
Current cash: 1027366.32
Portfolio value: 1027156.19
--------------------------------------------------------------------
Strategy  len: 15945
Data0 len: 15945
Data1 len: 15945
Data0 dt: 2017-07-25 23:15:00
Data1 dt: 2017-07-25 23:15:00
Data0 dt: 2017-07-25 23:15:00
Data1 dt: 2017-07-25 23:15:00
status is 1
--------------------------------------------------------------------
Current cash: 1027366.32
Portfolio value: 1027132.79
--------------------------------------------------------------------
Strategy  len: 15946
Data0 len: 15946
Data1 len: 15946
Data0 dt: 2017-07-25 23:20:00
Data1 dt: 2017-07-25 23:20:00
Data0 dt: 2017-07-25 23:20:00
Da

Data1 dt: 2017-07-27 01:50:00
Data0 dt: 2017-07-27 01:50:00
Data1 dt: 2017-07-27 01:50:00
status is 1
--------------------------------------------------------------------
Current cash: 1026332.98
Portfolio value: 1026701.70
--------------------------------------------------------------------
Strategy  len: 16055
Data0 len: 16055
Data1 len: 16055
Data0 dt: 2017-07-27 01:55:00
Data1 dt: 2017-07-27 01:55:00
Data0 dt: 2017-07-27 01:55:00
Data1 dt: 2017-07-27 01:55:00
status is 1
--------------------------------------------------------------------
Current cash: 1026332.98
Portfolio value: 1026673.23
--------------------------------------------------------------------
Strategy  len: 16056
Data0 len: 16056
Data1 len: 16056
Data0 dt: 2017-07-27 02:00:00
Data1 dt: 2017-07-27 02:00:00
Data0 dt: 2017-07-27 02:00:00
Data1 dt: 2017-07-27 02:00:00
status is 1
--------------------------------------------------------------------
Current cash: 1026332.98
Portfolio value: 1026562.30
--------------------

Strategy  len: 16164
Data0 len: 16164
Data1 len: 16164
Data0 dt: 2017-07-28 22:00:00
Data1 dt: 2017-07-28 22:00:00
Data0 dt: 2017-07-28 22:00:00
Data1 dt: 2017-07-28 22:00:00
status is 2
--------------------------------------------------------------------
Current cash: 1027641.95
Portfolio value: 1026519.25
--------------------------------------------------------------------
Strategy  len: 16165
Data0 len: 16165
Data1 len: 16165
Data0 dt: 2017-07-28 22:05:00
Data1 dt: 2017-07-28 22:05:00
Data0 dt: 2017-07-28 22:05:00
Data1 dt: 2017-07-28 22:05:00
status is 2
--------------------------------------------------------------------
Current cash: 1027641.95
Portfolio value: 1026188.23
--------------------------------------------------------------------
Strategy  len: 16166
Data0 len: 16166
Data1 len: 16166
Data0 dt: 2017-07-28 22:10:00
Data1 dt: 2017-07-28 22:10:00
Data0 dt: 2017-07-28 22:10:00
Data1 dt: 2017-07-28 22:10:00
status is 2
---------------------------------------------------------

Data1 dt: 2017-07-29 03:25:00
Data0 dt: 2017-07-29 03:25:00
Data1 dt: 2017-07-29 03:25:00
status is 2
--------------------------------------------------------------------
Current cash: 1027641.95
Portfolio value: 1026381.18
--------------------------------------------------------------------
Strategy  len: 16230
Data0 len: 16230
Data1 len: 16230
Data0 dt: 2017-07-29 03:30:00
Data1 dt: 2017-07-29 03:30:00
Data0 dt: 2017-07-29 03:30:00
Data1 dt: 2017-07-29 03:30:00
status is 2
--------------------------------------------------------------------
Current cash: 1027641.95
Portfolio value: 1026581.65
--------------------------------------------------------------------
Strategy  len: 16231
Data0 len: 16231
Data1 len: 16231
Data0 dt: 2017-07-29 03:35:00
Data1 dt: 2017-07-29 03:35:00
Data0 dt: 2017-07-29 03:35:00
Data1 dt: 2017-07-29 03:35:00
status is 2
--------------------------------------------------------------------
Current cash: 1027641.95
Portfolio value: 1026723.00
--------------------

In [187]:
results

[('JBT-MAN', 0.32375345301378183, 1000000, 1031886.8950000008, 0)]